# **Object Detection API TF2 Retraining Example using Colab and Google Drive**

> ## Creating personal Colab for retraining of an Object Detction API TF2 based model





>> #### [see this blog for original example](https://towardsdatascience.com/detailed-tutorial-build-your-custom-real-time-object-detector-5ade1017fd2d)





# STEP 1: Mount Google Drive 
##### to get access to data set and for storage of created training files (checkpoints, models, etc)

*  ***you must choose only Option A or B***




**Assumes following directory structure**

*  ***important: the csv, and record files will be generated in cells below***



```
project_directory/
        ├─ data/
        │    ├── images/
        │    │      ├── armas (1).jpg
        │    │      ├── armas (2).jpg
        │    │      └── ...
        │    ├── train_labels/
        │    │      ├── armas (1).xml
        │    │      ├── armas (2).xml
        │    │      └── ...
        │    ├── test_labels/
        │    │      ├── armas (10).xml
        │    │      ├── armas (20).xml
        │    │      └── ...
        │    ├── label_map.pbtxt
        │    ├── test_labels.csv
        │    ├── train_labels.csv
        │    ├── test_labels.record
        │    └── train_labels.record
        └─ models/
             ├─ research/
             │      ├── fine_tuned_model/
             │      │         ├── frozen_inference_graph.pb
             │      │         └── ...
             │      │         
             │      ├── pretrained_model/
             │      │         ├── frozen_inference_graph.pb
             │      │         └── ...
             │      │         
             │      ├── object_detection/
             │      │         ├── utils/
             │      │         ├── samples/
             │      │         │      ├── samples/ 
             │      │         │      │       ├── configs/             
             │      │         │      │       │     ├── ssd_mobilenet_v2_coco.config
             │      │         │      │       │     ├── rfcn_resnet101_pets.config
             │      │         │      │       │     └── ...
             │      │         │      │       └── ... 
             │      │         │      └── ...                                
             │      │         ├── export_inference_graph.py
             │      │         ├── model_main.py
             │      │         └── ...
             │      │         
             │      ├── training/
             │      │         ├── events.out.tfevents.xxxxx
             │      │         └── ...               
             │      └── ...
             └── ...




### mounting Google Drive via GUI in Colab and then with this code Access it

In [4]:
from google.colab import drive
drive.mount('/gdrive')

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


In [5]:
%ls /gdrive
%ls /gdrive/'Shared drives'/Covid_ID/RetrainColab
#base_dir = '/gdrive/Shared\ drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased'
base_dir = "/gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased"
print(base_dir)
%ls {base_dir}
data_dir = base_dir +  "/data"
%ls {data_dir}

#tell number of train label files
print("\n\ntrain_labels_dir")
train_labels_dir = data_dir + '/train_labels'
#%ls {train_labels_dir}
%ls -1 {train_labels_dir} | wc -l

#tell number of test label files
print("\n\ntest_labels_dir")
test_labels_dir = data_dir + '/test_labels'
#ls {test_labels_dir}
%ls -1 {test_labels_dir} | wc -l

#tell number of image files
print("\n\nimages_dir")
images_dir = data_dir + '/images'
#%ls {images_dir}
%ls -1 {images_dir} | wc -l


#create other directory path variables that will be used in this script
models_research_dir = base_dir + "/models/research"
object_detect_dir = models_research_dir + "/object_detection"
object_detect_protos = object_detect_dir + "/protos/*.protos"
%ls {object_detect_dir}

'My Drive'/  'Shared drives'/
DetectionWeaponsExample_CodeLabBased/
/gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased
data/                    models/    weapon_detection_BL.ipynb
datatrain_labels.record  training/  weapon_detection_BL_OLD.ipynb
images/          test_labels/        train_labels/        WeaponS_bbox.zip
label_map.pbtxt  test_labels.csv     train_labels.csv     WeaponS.zip
test_images/     test_labels.record  train_labels.record


train_labels_dir
2400


test_labels_dir
600


images_dir
3267
anchor_generators/                       inputs.py
box_coders/                              inputs_test.py
builders/                                legacy/
colab_tutorials/                         matchers/
configs/                                 meta_architectures/
CONTRIBUTING.md                          metrics/
core/                                    model_hparams.py
data/                                    model_lib.py
data_decoders/           

**========================================================================**

# STEP 2: Install Required Packages for Colab environment & setup
## (do every time you restart colab)
##### colab has install basic packages like Tensorflow,etc. but anything additional you will need to install next

***you can run !pip list to see what is currently installed***

In [6]:
print("Currently Installed")
!pip list

print("\n\n")
!sudo apt-get update   #update the location of packages in case they have moved
print("installing protobuf-compiler python-pil python-lxml and python-tk")
!apt-get install -qq protobuf-compiler python-pil python-lxml python-tk

print("\n\n")

print("installing Cython contextlib2 pillow lxml matplotlib")

!pip install -qq Cython contextlib2 pillow lxml matplotlib



print("\n\n")
print("installing pycocotools")

!pip install -qq pycocotools


Currently Installed
Package                       Version        
----------------------------- ---------------
absl-py                       0.9.0          
alabaster                     0.7.12         
albumentations                0.1.12         
altair                        4.1.0          
argon2-cffi                   20.1.0         
asgiref                       3.2.10         
astor                         0.8.1          
astropy                       4.0.1.post1    
astunparse                    1.6.3          
atari-py                      0.2.6          
atomicwrites                  1.4.0          
attrs                         19.3.0         
audioread                     2.1.8          
autograd                      1.3            
Babel                         2.8.0          
backcall                      0.2.0          
beautifulsoup4                4.6.3          
bleach                        3.1.5          
blis                          0.4.1          
bokeh         

**========================================================================**

# STEP 3: Import modules you will use  AND install Object Detection API for colab

In [13]:
from __future__ import division, print_function, absolute_import

import pandas as pd
import numpy as np
import csv

import re
import os
import io
import glob
import shutil
import urllib.request
import tarfile
import xml.etree.ElementTree as ET

import tensorflow.compat.v1 as tf
import cv2 

from PIL import Image
from collections import namedtuple, OrderedDict

from google.colab import files
#print out version of tf
print(tf.__version__)

2.3.0


## *DO ONLY ONCE (next cell)*
## Install Object Detection API  


In [ ]:
# DO ONLY ONCE
# downloads the models
%cd {base_dir}
!git clone --q https://github.com/tensorflow/models.git

/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased
fatal: destination path 'models' already exists and is not an empty directory.



## Put model/research/slim directory in the colab's path environment variables 
#### *(note it assume that you have the Object Detection API code on the Google Drive already ---see file structure at top)*

In [9]:
# MUST do each time restart colab kernel
# INSTALL Object Detection API inside the Colab, as sits above TF2
# this will take several minutes as it will copy over all of the object_detection files
# you have mounted in project_folder/models/research/object_detection
# as you can see by the output of this cell it copies them into the colab
# environment at build/lib/object_detection

#this this is what I need to make the object_detection get installed

print(models_research_dir)
%cd {models_research_dir}
#%ls
#!python setup.py install   # from the models/reasearch


#install tf_slim
!pip install tf_slim

/gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research


### DO ONLY ONCE (next cell)
### compile proto buffers

In [ ]:
# compiles the proto buffers
%cd {models_research_dir}
!protoc object_detection/protos/*.proto --python_out=.


/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
/env/python:./:./slim/


### Setup PYTHONPATH variables to include tf_slim and others

In [19]:
#WARNING: you must run the code from withing the models_research_dir because PYTHONPATH can not have ' ' around them for things
# like 'My Drive' or 'Shared drives'  --- see https://github.com/tensorflow/models/issues/8291
# exports PYTHONPATH environment var with research and slim paths
%cd {models_research_dir}
os.environ['PYTHONPATH'] += ':./:./slim/'
print(os.environ['PYTHONPATH'])
os.environ['PYTHONPATH'] += ':../official/:../../models'
print(os.environ['PYTHONPATH'])
os.environ['PYTHONPATH'] += ':./object_detection/:../models/research/'
print(os.environ['PYTHONPATH'])

/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
/env/python:./:./slim/:../official/:../../models:./:./slim/:../official/:../../models:./object_detection/:./:./slim/
/env/python:./:./slim/:../official/:../../models:./:./slim/:../official/:../../models:./object_detection/:./:./slim/:../official/:../../models
/env/python:./:./slim/:../official/:../../models:./:./slim/:../official/:../../models:./object_detection/:./:./slim/:../official/:../../models:./object_detection/:../models/research/


### OPTIONAL - DO AT MOST ONCE

In [ ]:
# optional test to see if install and compile went well
# testing the model builder

%cd {models_research_dir}
!python3 object_detection/builders/model_builder_test.py

/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
/env/python:./:./slim/:../official/:../../models
2020-08-13 03:09:26.046562: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
Traceback (most recent call last):
  File "object_detection/builders/model_builder_test.py", line 21, in <module>
    from object_detection.builders import model_builder
  File "/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/object_detection/builders/model_builder.py", line 20, in <module>
    from object_detection.builders import anchor_generator_builder
  File "/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/object_detection/builders/anchor_generator_builder.py", line 23, in <module>
    from object_detection.anchor_generators import flexible_grid_anchor_generator
  File "/gdrive/Shared drives/Covid_

**========================================================================**

# STEP 4: Preprocessing Data  --ONLY DO ONCE OR WHEN DATA CHANGES
*   convert images to correct size for model 
*   take xml files in train_labels and test_labels and make single train_labels.csv and test_labels.csv
*   create label_map.pbtext that lists classes and names
*   convert the images in images_dir and the single csv files to the TFRecord files train_labels.record and test_labels.record that will be use for faster data presentation in training

#### **Preprocessing Images and Labels**
1. Converting the annotations from xml files to two csv files for each `train_labels/` and `train_labels/`.
2. Creating a pbtxt file that specifies the number of class (one class in this case)
3. Checking if the annotations for each object are placed within the range of the image width and height.


**This will take a LONG time as it must read and parse every xml file**

In [11]:
print(data_dir)
%cd {data_dir}
%pwd
%ls {data_dir}

/gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
images/          test_labels/        train_labels/        WeaponS_bbox.zip
label_map.pbtxt  test_labels.csv     train_labels.csv     WeaponS.zip
test_images/     test_labels.record  train_labels.record


In [ ]:
#adjusted from: https://github.com/datitran/raccoon_dataset

#converts the annotations/labels into one csv file for each training and testing labels
#creats label_map.pbtxt file

%cd {data_dir}
%pwd
%ls {data_dir}

# images extension
images_extension = 'jpg'

# takes the path of a directory that contains xml files and converts
#  them to one csv file.

# returns a csv file that contains: image name, width, height, class, xmin, ymin, xmax, ymax.
# note: if the xml file contains more than one box/label, it will create more than one row for 
#the same image. each row contains the info for an individual box. 
def xml_to_csv(path):
  classes_names = []
  xml_list = []

  for xml_file in glob.glob(path + '/*.xml'):
    tree = ET.parse(xml_file)
    root = tree.getroot()
    for member in root.findall('object'):
      classes_names.append(member[0].text)
      value = (root.find('filename').text + '.' + images_extension,
               int(root.find('size')[0].text),
               int(root.find('size')[1].text),
               member[0].text,
               int(member[4][0].text),
               int(member[4][1].text),
               int(member[4][2].text),
               int(member[4][3].text))
      xml_list.append(value)
  column_name = ['filename', 'width', 'height', 'class', 'xmin', 'ymin', 'xmax', 'ymax']
  xml_df = pd.DataFrame(xml_list, columns=column_name) 
  classes_names = list(set(classes_names))
  classes_names.sort()
  return xml_df, classes_names

# for both the train_labels and test_labels csv files, it runs the xml_to_csv() above.
for label_path in ['train_labels', 'test_labels']:
  image_path = os.path.join(os.getcwd(), label_path)
  xml_df, classes = xml_to_csv(label_path)
  xml_df.to_csv(f'{label_path}.csv', index=None)
  print(f'Successfully converted {label_path} xml to csv.')

# Creating the `label_map.pbtxt` file
label_map_path = os.path.join("label_map.pbtxt")

pbtxt_content = ""

#creates a pbtxt file the has the class names.
for i, class_name in enumerate(classes):
    # display_name is optional.
    pbtxt_content = (
        pbtxt_content
        + "item {{\n    id: {0}\n    name: '{1}'\n    display_name: 'Gun'\n }}\n\n".format(i + 1, class_name)
    )
pbtxt_content = pbtxt_content.strip()
with open(label_map_path, "w") as f:
    f.write(pbtxt_content)


/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
images/          test_labels.csv     train_labels.csv     WeaponS.zip
label_map.pbtxt  test_labels.record  train_labels.record
test_labels/     train_labels/       WeaponS_bbox.zip
Successfully converted train_labels xml to csv.
Successfully converted test_labels xml to csv.


In [12]:
#checking the pbtxt file
%cd {data_dir}
%ls {data_dir}
%cat label_map.pbtxt

/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
images/          test_labels/        train_labels/        WeaponS_bbox.zip
label_map.pbtxt  test_labels.csv     train_labels.csv     WeaponS.zip
test_images/     test_labels.record  train_labels.record
item {
    id: 1
    name: 'pistol'
    display_name: 'Gun'
 }

#### **Generate TFRecords: Convert csv + images to TFRecord files (train_labels.record, test_lables.record**
1. Read in the train_labels.csv and the corresponding images to create a train_labels.record a TFRecord file
2. Read in the test_labels.csv and the corresponding images to create a test_labels.record a TFRecord file



# >> **HARD CODED MUST FIX: ** The following hard codes for the class pistol to convert to the class number 1. Need to read in the label_map.pbtxt file instead and parse it for multiple classes and create a map so can look up the id for the passed row_label ---see code below

In [15]:

#adjusted from: https://github.com/datitran/raccoon_dataset


%cd {models_research_dir}
from object_detection.utils import dataset_util

%cd {data_dir}


#change this to the base directory where your data/ is 
#data_base_url = '/gdrive/My Drive/Colab Notebooks/object_detection/data/'
data_base_url = '/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data/'


#location of images
image_dir = data_base_url +'images/'

def class_text_to_int(row_label):
  if row_label == 'pistol':
    return 1
  else:
    None

def split(df, group):
  data = namedtuple('data', ['filename', 'object'])
  gb = df.groupby(group)
  return [data(filename, gb.get_group(x)) for filename, x in zip(gb.groups.keys(), gb.groups)]

def create_tf_example(group, path):
	with tf.io.gfile.GFile(os.path.join(path, '{}'.format(group.filename)), 'rb') as fid:
	  encoded_jpg = fid.read()
   
	encoded_jpg_io = io.BytesIO(encoded_jpg)
	image = Image.open(encoded_jpg_io)
	width, height = image.size
	filename = group.filename.encode('utf8')
	image_format = b'jpg'
	xmins = []
	xmaxs = []
	ymins = []
	ymaxs = []
	classes_text = []
	classes = []
  

	for index, row in group.object.iterrows():
		xmins.append(row['xmin'] / width)
		xmaxs.append(row['xmax'] / width)
		ymins.append(row['ymin'] / height)
		ymaxs.append(row['ymax'] / height)
		classes_text.append(row['class'].encode('utf8'))
		classes.append(class_text_to_int(row['class']))

	tf_example = tf.train.Example(features=tf.train.Features(feature={
		'image/height': dataset_util.int64_feature(height),
		'image/width': dataset_util.int64_feature(width),
		'image/filename': dataset_util.bytes_feature(filename),
		'image/source_id': dataset_util.bytes_feature(filename),
		'image/encoded': dataset_util.bytes_feature(encoded_jpg),
		'image/format': dataset_util.bytes_feature(image_format),
		'image/object/bbox/xmin': dataset_util.float_list_feature(xmins),
		'image/object/bbox/xmax': dataset_util.float_list_feature(xmaxs),
		'image/object/bbox/ymin': dataset_util.float_list_feature(ymins),
		'image/object/bbox/ymax': dataset_util.float_list_feature(ymaxs),
		'image/object/class/text': dataset_util.bytes_list_feature(classes_text),
		'image/object/class/label': dataset_util.int64_list_feature(classes),
		}))
	return tf_example
#creates tfrecord for both csv's
for csv in ['train_labels', 'test_labels']:
  print("Parsing csv: ", csv)
  writer = tf.io.TFRecordWriter(data_base_url + csv + '.record')
  path = os.path.join(image_dir)
  examples = pd.read_csv(data_base_url + csv + '.csv')
  grouped = split(examples, 'filename')
  for group in grouped:
    tf_example = create_tf_example(group, path)
    writer.write(tf_example.SerializeToString())
    
  writer.close()
  output_path = os.path.join(os.getcwd(), data_base_url + csv + '.record')
  print('Successfully created the TFRecords: {}'.format(data_base_url +csv + '.record'))


/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
Parsing csv:  train_labels
Successfully created the TFRecords: /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data/train_labels.record
Parsing csv:  test_labels
Successfully created the TFRecords: /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data/test_labels.record


**========================================================================**


# STEP 5: Training Model

*   using selected model retrain 
*   Input expected is TFRecord for training and evaluation




### Select model wish to retrain from object detection api set of pretrained models  AND specify some basic training parameters

In [20]:
##change chosen model to deploy different models available in the TF2 object detection zoo
MODELS_CONFIG = {
    'efficientdet-d0': {
        'model_name': 'efficientdet_d0_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d0_512x512_coco17_tpu-8.config',
        'pretrained_checkpoint': 'efficientdet_d0_coco17_tpu-32.tar.gz',
        'batch_size': 16
    },
    'efficientdet-d1': {
        'model_name': 'efficientdet_d1_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d1_640x640_coco17_tpu-8.config',
        'pretrained_checkpoint': 'efficientdet_d1_coco17_tpu-32.tar.gz',
        'batch_size': 16
    },
    'efficientdet-d2': {
        'model_name': 'efficientdet_d2_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d2_768x768_coco17_tpu-8.config',
        'pretrained_checkpoint': 'efficientdet_d2_coco17_tpu-32.tar.gz',
        'batch_size': 16
    },
        'efficientdet-d3': {
        'model_name': 'efficientdet_d3_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d3_896x896_coco17_tpu-32.config',
        'pretrained_checkpoint': 'efficientdet_d3_coco17_tpu-32.tar.gz',
        'batch_size': 16
    }
}

#in this tutorial we implement the lightweight, smallest state of the art efficientdet model
#if you want to scale up tot larger efficientdet models you will likely need more compute!
chosen_model = 'efficientdet-d0'

num_steps = 16000 #40,000 The more steps, the longer the training. Increase if your loss function is still decreasing and validation metrics are increasing. 
num_eval_steps = 500 #Perform evaluation after so many steps

model_name = MODELS_CONFIG[chosen_model]['model_name']
pretrained_checkpoint = MODELS_CONFIG[chosen_model]['pretrained_checkpoint']
base_pipeline_file = MODELS_CONFIG[chosen_model]['base_pipeline_file']
batch_size = MODELS_CONFIG[chosen_model]['batch_size'] #if you can fit a large batch in memory, it may speed up your training


print("Model Chosen for Retraining")
print(" name "+ model_name)
print(" pretrained_checkpoint " + pretrained_checkpoint)
print(" base_pipeline_file " + base_pipeline_file)
print(" batch_size " + str(batch_size))

Model Chosen for Retraining
 name efficientdet_d0_coco17_tpu-32
 pretrained_checkpoint efficientdet_d0_coco17_tpu-32.tar.gz
 base_pipeline_file ssd_efficientdet_d0_512x512_coco17_tpu-8.config
 batch_size 16


### specify the TFRecord files for training

In [21]:
# See previous cell where created record files for location and name of files
%cd {data_dir}
test_record_fname =  str(os.getcwd()) + os.path.sep + "train_labels.record"
train_record_fname = str(os.getcwd()) + os.path.sep + "test_labels.record"
%cd {data_dir}
label_map_pbtxt_fname =  str(os.getcwd()) + os.path.sep + "label_map.pbtxt"


    
print("Files used in Training")
print(test_record_fname)
print(train_record_fname)
print(label_map_pbtxt_fname)

/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data
Files used in Training
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data/train_labels.record
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data/test_labels.record
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/data/label_map.pbtxt


### DO ONLY ONCE
### get the pretrained model and put it into a special new deploy directory 

In [16]:
#DO ONLY ONCE

#download pretrained weights
deploy_path = models_research_dir + "/deploy/"
#%mkdir /content/models/research/deploy/
%mkdir {deploy_path}
%cd {deploy_path}
#%cd /content/models/research/deploy/

    
import tarfile
download_tar = 'http://download.tensorflow.org/models/object_detection/tf2/20200711/' + pretrained_checkpoint

!wget {download_tar}
tar = tarfile.open(pretrained_checkpoint)
tar.extractall()
tar.close()

mkdir: cannot create directory ‘/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/’: File exists
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy
--2020-08-13 23:45:21--  http://download.tensorflow.org/models/object_detection/tf2/20200711/efficientdet_d0_coco17_tpu-32.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 74.125.195.128, 2607:f8b0:400e:c09::80
Connecting to download.tensorflow.org (download.tensorflow.org)|74.125.195.128|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 30736482 (29M) [application/x-tar]
Saving to: ‘efficientdet_d0_coco17_tpu-32.tar.gz.1’

efficientdet_d0_coc 100%[===================>]  29.31M  59.9MB/s    in 0.5s    

2020-08-13 23:45:21 (59.9 MB/s) - ‘efficientdet_d0_coco17_tpu-32.tar.gz.1’ saved [30736482/30736482]



### DO ONLY ONCE
### now get the pretrained model's configuration file and put it in the deploy directory created in cell above

In [ ]:
%cd {deploy_path}
download_config = 'https://raw.githubusercontent.com/tensorflow/models/master/research/object_detection/configs/tf2/' + base_pipeline_file
!wget {download_config}

/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy
--2020-08-13 05:05:37--  https://raw.githubusercontent.com/tensorflow/models/master/research/object_detection/configs/tf2/ssd_efficientdet_d0_512x512_coco17_tpu-8.config
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4630 (4.5K) [text/plain]
Saving to: ‘ssd_efficientdet_d0_512x512_coco17_tpu-8.config.1’

ssd_efficientdet_d0 100%[===================>]   4.52K  --.-KB/s    in 0.001s  

2020-08-13 05:05:37 (3.87 MB/s) - ‘ssd_efficientdet_d0_512x512_coco17_tpu-8.config.1’ saved [4630/4630]



### setup parameters to pass to training script for Object Detect API on TF2


*   pipeline_filename = the configuration file for training
*   fine_tune_checkpoint = checkpoint file of model will retrain that you will start from
*   num_classes= number of classes you will retrain to (from your label file)



In [28]:
# at C:\tensorflow\models\research\object_detection\utils\label_map_util.py
# rather than the tf2 version installed in this jupyter notebooks
# environment it is launched from which is tf2
# because the import below in the function get_num_classes
#   "from object_detection.utils import label_map_util"
# is mapping to wrong object detection api
#prepare
print(" Version of tf " + tf.__version__)

#pipeline_fname = deploy_path + base_pipeline_file
#fine_tune_checkpoint = deploy_path + model_name + '/checkpoint/ckpt-0'
%cd {deploy_path}
pipeline_fname = str(os.getcwd()) + os.path.sep + base_pipeline_file
fine_tune_checkpoint = str(os.getcwd()) + os.path.sep + model_name + '/checkpoint/ckpt-0'



print("pipeline_fname " + pipeline_fname)
print("fine_tune_checkpoint " + fine_tune_checkpoint)



    
def get_num_classes(pbtxt_fname):
    from object_detection.utils import label_map_util
    label_map = label_map_util.load_labelmap(pbtxt_fname)
    categories = label_map_util.convert_label_map_to_categories(
        label_map, max_num_classes=90, use_display_name=True)
    category_index = label_map_util.create_category_index(categories)
    return len(category_index.keys())

#WARNING:  you must use relative path as 'My Drive' or 'Shared drives' in a path will fail to open or find
# the file in the get_num_classes function ....so cd to directory and call with local filename
# need to be in the models/research directory when execute the get_num_classes function as it needs to find object_detection
relative_path_to_labelfile = "../../data/label_map.pbtxt"
print(relative_path_to_labelfile)
#num_classes = get_num_classes(label_map_pbtxt_fname)
%cd {models_research_dir}
print("--------------")
%ls
num_classes = get_num_classes(relative_path_to_labelfile)


print("Number of classes= "+ str(num_classes))
print("Label file "+ label_map_pbtxt_fname)

 Version of tf 2.3.0
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy
pipeline_fname /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/ssd_efficientdet_d0_512x512_coco17_tpu-8.config
fine_tune_checkpoint /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/efficientdet_d0_coco17_tpu-32/checkpoint/ckpt-0
../../data/label_map.pbtxt
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
--------------
a3c_blogpost/        cvt_text/       lfads/                      README.md
adversarial_text/    deeplab/        lstm_object_detection/      rebar/
attention_ocr/       deep_speech/    marco/                      setup.py
audioset/            delf/           nst_blogpost/               slim/
autoaugment/         deploy/         object_detection/           vid2depth/
build/               dist/  

### Modify the configuration file to update with some training values

In [ ]:
#write custom configuration file by slotting our dataset, model checkpoint, and training parameters into the base pipeline file

import re
import pathlib

%cd {deploy_path}

    
print(" path cwd " + str(pathlib.Path.cwd()))
print("reading original configuration file name= " + str(pipeline_fname))

print("writing custom configuration file name= " + str(os.getcwd()) + os.path.sep + "pipeline_file.config")
      
      
with open(pipeline_fname) as f:
    s = f.read()
with open('pipeline_file.config', 'w') as f:
    
    # fine_tune_checkpoint
    s = re.sub('fine_tune_checkpoint: ".*?"',
               'fine_tune_checkpoint: "{}"'.format(fine_tune_checkpoint), s)
    
    # tfrecord files train and test.
    s = re.sub(
        '(input_path: ".*?)(PATH_TO_BE_CONFIGURED/train)(.*?")', 'input_path: "{}"'.format(train_record_fname), s)
    s = re.sub(
        '(input_path: ".*?)(PATH_TO_BE_CONFIGURED/val)(.*?")', 'input_path: "{}"'.format(test_record_fname), s)

    # label_map_path
    s = re.sub(
        'label_map_path: ".*?"', 'label_map_path: "{}"'.format(label_map_pbtxt_fname), s)

    # Set training batch_size.
    s = re.sub('batch_size: [0-9]+',
               'batch_size: {}'.format(batch_size), s)

    # Set training steps, num_steps
    s = re.sub('num_steps: [0-9]+',
               'num_steps: {}'.format(num_steps), s)
    
    # Set number of classes num_classes.
    s = re.sub('num_classes: [0-9]+',
               'num_classes: {}'.format(num_classes), s)
    
    #fine-tune checkpoint type
    s = re.sub(
        'fine_tune_checkpoint_type: "classification"', 'fine_tune_checkpoint_type: "{}"'.format('detection'), s)
        
    f.write(s)


    # problem --can't open files with ' ' inside the pathname 


/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy
 path cwd /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy
reading original configuration file name= /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/ssd_efficientdet_d0_512x512_coco17_tpu-8.config
writing custom configuration file name= /gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/pipeline_file.config


In [29]:
config_file = deploy_path + "pipeline_file.config"
print(config_file)
%cat {config_file}

/gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/pipeline_file.config
 # SSD with EfficientNet-b0 + BiFPN feature extractor,
# shared box predictor and focal loss (a.k.a EfficientDet-d0).
# See EfficientDet, Tan et al, https://arxiv.org/abs/1911.09070
# See Lin et al, https://arxiv.org/abs/1708.02002
# Trained on COCO, initialized from an EfficientNet-b0 checkpoint.
#
# Train on TPU-8

model {
  ssd {
    inplace_batchnorm_update: true
    freeze_batchnorm: false
    num_classes: 1
    add_background_class: false
    box_coder {
      faster_rcnn_box_coder {
        y_scale: 10.0
        x_scale: 10.0
        height_scale: 5.0
        width_scale: 5.0
      }
    }
    matcher {
      argmax_matcher {
        matched_threshold: 0.5
        unmatched_threshold: 0.5
        ignore_thresholds: false
        negatives_lower_than_unmatched: true
        force_match_for_each_row: true
        use_matmul_gather: true
      }
    }
    s

##run the trainer by calling a script for Obj Detect API on TF2 called model_main_tf2 which takes the following parameters


*   pipeline_file = configuration file used in training created in previous stem
*   model_dir = directory where will write results of training including checkpoints and tensorboard event file.



In [ ]:

pipeline_file = deploy_path + 'pipeline_file.config'
model_dir = base_dir + '/training/'

print(" options")
print("    pipeline_config_path= "+ pipeline_file)
print("    model_dir= " + model_dir)
print("    alsologtostderr")
print("    num_train_steps= "+ str(num_steps))
print("    sample_1_of_n_eval_examples= " + str(1))
print("    num_eval_steps= " + str(num_eval_steps))

training_script = object_detect_dir + "/model_main_tf2.py"

#must be in the diretory that the object_detection folder is stored (models/research)
%cd {models_research_dir}
#!python /content/models/research/object_detection/model_main_tf2.py \
!python {training_script} \
        --pipeline_config_path={pipeline_file} \
        --model_dir={model_dir} \
        --alsologtostderr \
        --num_train_steps={num_steps} \
        --sample_1_of_n_eval_examples=1 \
        --num_eval_steps={num_eval_steps}

 options
    pipeline_config_path= /gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research/deploy/pipeline_file.config
    model_dir= /gdrive/'Shared drives'/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/training/
    alsologtostderr
    num_train_steps= 16000
    sample_1_of_n_eval_examples= 1
    num_eval_steps= 500
/gdrive/Shared drives/Covid_ID/RetrainColab/DetectionWeaponsExample_CodeLabBased/models/research
2020-08-14 00:00:17.668104: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
2020-08-14 00:00:20.244344: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
2020-08-14 00:00:20.288117: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:982] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2020-08-14 00:00:20.

In [ ]:
#see where our model saved weights...
%ls {model_dir}
#os.listdir(r'C:\Users\Lynne\TensorFlowExamples\maskDetectRoboflowSet\training')

**========================================================================**

# Save Model

In [ ]:

#run conversion script
import re
import numpy as np


output_directory = base_dir + '/fine_tuned_model'

#place the model weights you would like to export here
last_model_path = model_dir



script_file = BASE_PATH + os.path.sep + "object_detection" + os.path.sep + "exporter_main_v2.py"
    
print(last_model_path)
print(script_file)
print(pipeline_file)
print(output_directory)
!python /content/models/research/object_detection/exporter_main_v2.py \
  --trained_checkpoint_dir {last_model_path} --output_directory {output_directory} --pipeline_config_path {pipeline_file}

In [ ]:
#display directory of SavedModel

saved_model_path = base_dir + '/fine_tuned_model/saved_model/'

print(saved_model_path)
    
%ls {saved_model_path}

**========================================================================**

# Run Tensorboard on results

In [ ]:
# first install it
!pip install tensorboard


logs_dir = base_dir + "/training/train"

# launch tensorboard
!tensorboard --logdir logs_dir

**========================================================================**

# Predict on single randomly selected Test images